# Final Capstone Project

### Introduction

The region of Flanders, Belgium, is one of the most densily populated region in Western Europe and also an economic hub, enjoying its citizens a high level of GDP per capita. In this exercise, we want to compare the neighborhoods across 3 different cities in order to understand the similarities among them so we can chose where we could potentially chose which city to move into and into which neighborhood.

The three cities are:
- Antwerpen, the capital of the region. It is the largest of the three and host the second biggest harbour in Europe
- Leuven, second biggest city of the region and cultural hub
- Genk, smaller provincial city, much smaller in terms of population

### Data

Two different data sets were used, both from the official Belgium Statistics Open Data repository (https://statbel.fgov.be/en/open-data?category=All)
- Statistical sectors 2020 https://statbel.fgov.be/en/open-data/statistical-sectors-2020 --> This is the minimum administrative sub-division 
- Population by statistical sector 2020 https://statbel.fgov.be/en/open-data/population-statistical-sector-8

At the start of this exercise, it is unclear if Population by statistical sector will be needed nevertheless it was decided to include it.

The data was prepared in QGIS and Excel as follows:
1. Change coordinate system to geographical coordinate system WGS 84 EPSG:4326, so the coordinates will come in decimal degrees, by means of Saving Layer As with different coordinate system
2. In Excel, save Population by statistical sector 2020 in CSV
3. Join attribute tables of imported CSV with those of the Statistical Sectors
4. Calculate centroids of Statistical Sectors, so we get points instead of polygons
6. Calculate geometry attributes of centroids
7. Create different data sets by cities of interest (Antwerpen, Leuven, Genk)

For the clustering, Foursquare API will be used to extract the venues in the neighborhoods.

For visualization purposes, OpenStreetMaps data is used for the background maps.

Pre-processing of data will be done in this notebook and therefore will be explained in the methodology section.

### Methodology

We start by importing all different libraries, including geopandas to import the shp files

In [1]:
import pandas as pd
import geopandas
import matplotlib.pyplot as plt
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import folium
import requests
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import numpy as np

We chose a mid location in Flanders, Putte, so we can see both cities at the same time

In [2]:
address = 'Putte, Belgium'

geolocator = Nominatim(user_agent="ca_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

The geograpical coordinate of Putte, Belgium are 51.0570823, 4.6310473.


Next, we import the shapefiles of the three cities with geopandas. Initially we had 5 cities but Foursquare didnt allow to download that much data without subscription

In [3]:
Antw = geopandas.read_file('./data/GIS files/NeighborhoodsAntwerpen.shp')
Leuv = geopandas.read_file('./data/GIS files/NeighborhoodsLeuven.shp')
#Gent = geopandas.read_file('./data/GIS files/NeighborhoodsGent.shp')
Genk = geopandas.read_file('./data/GIS files/NeighborhoodsGenk.shp')
#Brus = geopandas.read_file('./data/GIS files/NeighborhoodsBrussels.shp')

We add all geodataframes together so we can cluster them together afterwards and compare neighborhoods regardless of the city. If we would want to include more cities, we could modify the Cities_list array

In [4]:
Cities_list = [Antw, Leuv, Genk]
Cities = pd.concat(Cities_list)

Since there are a lot of columns with information that it is not relevant, we drop them

In [5]:
drop_columns = ['T_SEC_FR', 'T_SEC_DE', 'T_NIS6_FR', 'CNIS5_2020', 'T_MUN_FR', 'T_MUN_DE', 'C_ARRD',
       'T_ARRD_NL', 'T_ARRD_FR', 'T_ARRD_DE', 'C_PROVI', 'T_PROVI_NL',
       'T_PROVI_FR', 'T_PROVI_DE', 'C_REGIO', 'T_REGIO_NL', 'T_REGIO_FR',
       'T_REGIO_DE', 'C_COUNTRY', 'NUTS1', 'NUTS2', 'NUTS3', 'OPENDATA_S', 'OPENDATA_1', 'OPENDATA_2',
       'OPENDATA_3', 'OPENDATA_4', 'OPENDATA_5', 'OPENDATA_6', 'OPENDATA_7']
Cities.drop(columns = drop_columns, inplace=True)
Cities

CS01012020                                      T_SEC_NL  C_NIS6  \
0   1100212MQ                                      STABROEK  110021   
1   11002A00-  ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )  11002A   
2   11002A01-                      KLAPDORP - BROUWERSVLIET  11002A   
3   11002A02-                  GROENPLAATS (SPAANSE WALLEN)  11002A   
4   11002A03-                   HOOGSTRAAT (SPAANSE WALLEN)  11002A   
..        ...                                           ...     ...   
48  71016B242                                 NIEUWE KEMPEN  71016B   
49  71016B273                                     WOLFSBERG  71016B   
50  71016B29-                  ZWARTBERG-KOOLMIJN-VLIEGVELD  71016B   
51  71016B2AA                                ZWARTBERG-ZUID  71016B   
52  71016B2BA                              NIEUW-DRIEHOEVEN  71016B   

                              T_NIS6_NL   T_MUN_NL   M_AREA_HA  M_PERI_M  \
0           WIJZIGING VAN GEMEENTEGRENS  Antwerpen   81.007781    5228.0   
1   1-2-3-4 ADMINISTR. WIJK OF DISTRICT  Antwerpen   22.257464    2208.0   
2   1-2-3-4 ADMINISTR. WIJK OF DISTRICT  Antwerpen   13.816001    1753.0   
3   1-2-3-4 ADMINISTR. WIJK OF DISTRICT  Antwerpen   10.901108    1343.0   
4   1-2-3-4 ADMINISTR. WIJK OF DISTRICT  Antwerpen    9.244515    1212.0   
..                                  ...        ...         ...       ...   
48               WATERSCHEI - ZWARTBERG       Genk   91.773174    6146.0   
49               WATERSCHEI - ZWARTBERG       Genk  115.502537    7052.0   
50               WATERSCHEI - ZWARTBERG       Genk  252.703010   10414.0   
51               WATERSCHEI - ZWARTBERG       Genk   48.027172    3245.0   
52               WATERSCHEI - ZWARTBERG       Genk   15.886523    1585.0   

    Density  OPENDATA_8       lon        lat                  geometry  
0         0           0  4.341878  51.329844  POINT (4.34188 51.32984)  
1       125        2788  4.400889  51.222503  POINT (4.40089 51.22250)  
2       115        1595  4.403601  51.225234  POINT (4.40360 51.22523)  
3        49         537  4.402588  51.219115  POINT (4.40259 51.21911)  
4       114        1053  4.398159  51.219379  POINT (4.39816 51.21938)  
..      ...         ...       ...        ...                       ...  
48       20        1845  5.491861  51.012518  POINT (5.49186 51.01252)  
49        0          12  5.478330  51.004559  POINT (5.47833 51.00456)  
50        0          83  5.515443  51.013665  POINT (5.51544 51.01367)  
51       39        1857  5.502997  51.007247  POINT (5.50300 51.00725)  
52       34         546  5.492400  51.006164  POINT (5.49240 51.00616)  

[470 rows x 12 columns]

After dropping them, we rename the remaining columns for clarity

In [6]:
rename_columns = ['Code1', 'Name', 'Code2', 'Name2', 'Municipality', 'Area_ha', 'Peri_m', 'Density', 'Population', 'Lon', 'Lat', 'Geometry']
Cities.columns = rename_columns

Time to visualize the neighborhoods in the map.

In [7]:
# create map using latitude and longitude values
map_city = folium.Map(location=[latitude, longitude], zoom_start=9)

# add markers to map
for lat, lon, Code1, Name in zip(Cities['Lat'], Cities['Lon'], Cities['Code1'], Cities['Name']):
    label = '{}, {}'.format(Code1, Name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=0.5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7,
        parse_html=False).add_to(map_city)  
    
map_city

Next, we will implement the code for downloading the venues. We chose a radios of 200 m which seems appropriate due to the distance between neighborhoods, so there is not much overlap

In [8]:
CLIENT_ID = 'G4CN4VUVBD0EFCCT0LXPFSLWKJAHXJT2BPMPOD235BCMQ1N4' # your Foursquare ID
CLIENT_SECRET = '2C5510CMN0A2BBHX2JTJWNYBVRU4S5CXZJD3P3LCK5H0FVFN' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

In [9]:
def getNearbyVenues(names, latitudes, longitudes, radius=200):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [10]:
city_venues = getNearbyVenues(names=Cities['Name'],
                                   latitudes=Cities['Lat'],
                                   longitudes=Cities['Lon']
                                  )

STABROEK


KeyError: 'groups'

Below, a bit of exploratory analysis of the resulting dataframe

In [88]:
print(city_venues.shape)
city_venues.head()

(2321, 7)


Neighborhood  Neighborhood Latitude  \
0                                      STABROEK              51.329844   
1                                      STABROEK              51.329844   
2  ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )              51.222503   
3  ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )              51.222503   
4  ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )              51.222503   

   Neighborhood Longitude               Venue  Venue Latitude  \
0                4.341878  kaai 734 zuidnatie       51.329007   
1                4.341878   Becomar Zuidnatie       51.330475   
2                4.400889         Grote Markt       51.221163   
3                4.400889            Bia Mara       51.220894   
4                4.400889      De Pottekijker       51.221097   

   Venue Longitude      Venue Category  
0         4.343253                Port  
1         4.343896     Harbor / Marina  
2         4.399810               Plaza  
3         4.400189   Fish & Chips Shop  
4         4.401870  Belgian Restaurant

In [89]:
city_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                           
'T EILANDJE                                                       19   
'T FORT                                                            3   
'T LAAR                                                            5   
'T MESTPUTTEKE                                                    10   
ALBERTPARK (OOSTWIJK)                                              7   
AN-HAVEN/VORMINGSSTATION                                           3   
AN-LUCHTBAL-NOORD                                                  2   
ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )                      25   
ARENA                                                              2   
ASTRID BAD (OOSTWIJK)                                              4   
ATHENEUM (STATIONSWIJK)                                            2   
BANKSTRAAT                                                         6   
BEERSCHOT - STADION (KIEL)                                         1   
BELL (ZUIDWIJK)                                                    9   
BELLE VUE                                                          4   
BENEDEN KESSEL                                                     4   
BENEDEN-LO                                                         1   
BERCHEMBOS                                                         1   
BERENDRECHT - KERN (BERENDRECHT - 4 DISTRICT)                      5   
BISSCHOPPENHOF                                                     2   
BLANCEFLOERLAAN  (LINKEROEVER)                                     3   
BLAUWPUT-CENTRUM                                                  16   
BLIJDE INKOMSTSTRAAT                                              18   
BLOKKEN-KRUISHOFSTR. (WILR.PL)                                     6   
BOEKENBERG                                                         4   
BOEKENBERGLEI                                                     15   
BOEKENBERGPARK                                                     6   
BOELAERPARK-NOORD                                                  6   
BONDGENOTENLAAN                                                   13   
BOOLEEG                                                            1   
BOOMSE STWG-BEERSCHOT (KIEL)                                      10   
BORGERHOUT - GEMEENTEHUIS                                          5   
BOTERLAAR - SILSBURG                                               2   
BOTERLAARHOF                                                       4   
BOVEN-LO                                                           4   
BRABANCONNESTRAAT                                                  3   
BREM                                                               1   
BRUINE VELD                                                        3   
BRUUL                                                              8   
C. TEICHMANN PLAATS (ZUIDWIJK)                                     3   
CAMPUS HEVERLEE                                                    4   
CENTRALE GEVANGENIS                                                1   
CENTRALE WERKPLAATSEN                                             12   
CHARLES DE COSTERLAAN(L.OEVER)                                     2   
CHARLOTTALEI (OOSTWIJK)                                            5   
COLLEGE                                                            1   
CONFORTA                                                           6   
CRUYSLEI                                                          13   
DAGERAADPLAATS - OOSTSTATIE (OOSTWIJK)                            33   
DAM (DAM - SCHIJNPOORT)                                           17   
DAM- LOBROEKDOK (SCHIJNPOORT)                                      3   
DAMBRUGGESTRAAT-N.(STATIONSW.)                                     6   
DAMIAANPLEIN                                                       5   
DE BIST                                                            2   
DE BRUYNLAAN-NO

In [90]:
print('There are {} uniques categories.'.format(len(city_venues['Venue Category'].unique())))
print(city_venues['Venue Category'].unique())

There are 305 uniques categories.
['Port' 'Harbor / Marina' 'Plaza' 'Fish & Chips Shop' 'Belgian Restaurant'
 'Coffee Shop' 'French Restaurant' 'Bookstore' 'Italian Restaurant'
 'Steakhouse' 'Church' 'Restaurant' 'Fishing Store' 'Hotel'
 'Adult Boutique' 'History Museum' 'Gay Bar' 'Thai Restaurant'
 'Ethiopian Restaurant' 'Café' 'Soup Place' 'Empanada Restaurant' 'Bar'
 'American Restaurant' 'Health & Beauty Service' 'Nightclub' 'Waterfront'
 'Snack Place' 'Asian Restaurant' 'Greek Restaurant' 'Juice Bar'
 'Beer Bar' 'Frozen Yogurt Shop' 'Indonesian Restaurant' 'Cocktail Bar'
 'Deli / Bodega' 'Kitchen Supply Store' 'Clothing Store' 'Brasserie'
 'Vegetarian / Vegan Restaurant' 'Boutique' 'Gourmet Shop'
 'Sushi Restaurant' 'Perfume Shop' 'Burger Joint' 'Gaming Cafe'
 'Camera Store' 'Optical Shop' 'Cupcake Shop' 'Falafel Restaurant'
 'Pie Shop' 'Taco Place' 'Wine Bar' 'Ice Cream Shop' 'Art Museum'
 'Comfort Food Restaurant' 'Breakfast Spot' 'Mexican Restaurant'
 'Moroccan Restaurant' 'Bis

We start preparing the dataset for the clustering with the onehot

In [91]:
# one hot encoding
city_onehot = pd.get_dummies(city_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
city_onehot['Neighborhood'] = city_venues['Neighborhood'] 

city_onehot.head()

ATM  Adult Boutique  African Restaurant  American Restaurant  Aquarium  \
0    0               0                   0                    0         0   
1    0               0                   0                    0         0   
2    0               0                   0                    0         0   
3    0               0                   0                    0         0   
4    0               0                   0                    0         0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                     0                 0                   0            0   
1                     0                 0                   0            0   
2                     0                 0                   0            0   
3                     0                 0                   0            0   
4                     0                 0                   0            0   

   BBQ Joint  Bagel Shop  Bakery  Bar  Baseball Field  Basketball Court  \
0          0           0       0    0               0                 0   
1          0           0       0    0               0                 0   
2          0           0       0    0               0                 0   
3          0           0       0    0               0                 0   
4          0           0       0    0               0                 0   

   Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  \
0           0      0          0                0         0            0   
1           0      0          0                0         0            0   
2           0      0          0                0         0            0   
3           0      0          0                0         0            0   
4           0      0          0                0         0            0   

   Beer Store  Belgian Restaurant  Bike Rental / Bike Share  Bike Shop  \
0           0                   0                         0          0   
1           0                   0                         0          0   
2           0                   0                         0          0   
3           0                   0                         0          0   
4           0                   1                         0          0   

   Bike Trail  Bistro  Board Shop  Boat or Ferry  Bookstore  Botanical Garden  \
0           0       0           0              0          0                 0   
1           0       0           0              0          0                 0   
2           0       0           0              0          0                 0   
3           0       0           0              0          0                 0   
4           0       0           0              0          0                 0   

   Boutique  Bowling Alley  Bowling Green  Brasserie  Brazilian Restaurant  \
0         0              0              0          0                     0   
1         0              0              0          0                     0   
2         0              0              0          0                     0   
3         0              0              0          0                     0   
4         0              0              0          0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Buffet  \
0               0        0            0       0                0       0   
1               0        0            0       0                0       0   
2               0        0            0       0                0       0   
3            

In [92]:
# move neighborhood column to the first column
fixed_columns = [city_onehot.columns[-1]] + list(city_onehot.columns[:-1])
city_onehot = city_onehot[fixed_columns]

city_onehot.head()

Zoo Exhibit  ATM  Adult Boutique  African Restaurant  American Restaurant  \
0            0    0               0                   0                    0   
1            0    0               0                   0                    0   
2            0    0               0                   0                    0   
3            0    0               0                   0                    0   
4            0    0               0                   0                    0   

   Aquarium  Argentinian Restaurant  Art Gallery  Art Museum  \
0         0                       0            0           0   
1         0                       0            0           0   
2         0                       0            0           0   
3         0                       0            0           0   
4         0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auto Garage  BBQ Joint  Bagel Shop  Bakery  Bar  \
0                   0            0          0           0       0    0   
1                   0            0          0           0       0    0   
2                   0            0          0           0       0    0   
3                   0            0          0           0       0    0   
4                   0            0          0           0       0    0   

   Baseball Field  Basketball Court  Bath House  Beach  Beach Bar  \
0               0                 0           0      0          0   
1               0                 0           0      0          0   
2               0                 0           0      0          0   
3               0                 0           0      0          0   
4               0                 0           0      0          0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            0           0                   1   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0              0          0                 0         0              0   
1              0          0                 0         0              0   
2              0          0                 0         0              0   
3              0          0                 0         0              0   
4              0          0                 0         0              0   

   Bowling Green  Brasserie  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0          0                     0               0        0   
1              0          0                     0               0        0   
2              0          0                     0               0        0   
3              0          0                     0               0        0   
4              0          0                     0               0        0   

   Bridal Shop  Bridge  Bubble Tea Shop  Buffet  Burger Jo

In [93]:
city_grouped = city_onehot.groupby('Neighborhood').mean().reset_index()
city_grouped

Neighborhood  Zoo Exhibit       ATM  \
0                                      'T EILANDJE     0.000000  0.000000   
1                                          'T FORT     0.000000  0.000000   
2                                          'T LAAR     0.000000  0.000000   
3                                   'T MESTPUTTEKE     0.000000  0.000000   
4                            ALBERTPARK (OOSTWIJK)     0.000000  0.000000   
5                         AN-HAVEN/VORMINGSSTATION     0.000000  0.000000   
6                                AN-LUCHTBAL-NOORD     0.000000  0.000000   
7     ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )     0.000000  0.000000   
8                                            ARENA     0.000000  0.000000   
9                            ASTRID BAD (OOSTWIJK)     0.000000  0.000000   
10                         ATHENEUM (STATIONSWIJK)     0.000000  0.000000   
11                                      BANKSTRAAT     0.000000  0.000000   
12                      BEERSCHOT - STADION (KIEL)     0.000000  0.000000   
13                                 BELL (ZUIDWIJK)     0.000000  0.000000   
14                                       BELLE VUE     0.000000  0.000000   
15                                  BENEDEN KESSEL     0.000000  0.000000   
16                                      BENEDEN-LO     0.000000  0.000000   
17                                      BERCHEMBOS     0.000000  0.000000   
18   BERENDRECHT - KERN (BERENDRECHT - 4 DISTRICT)     0.000000  0.000000   
19                                  BISSCHOPPENHOF     0.000000  0.000000   
20                  BLANCEFLOERLAAN  (LINKEROEVER)     0.000000  0.000000   
21                                BLAUWPUT-CENTRUM     0.000000  0.000000   
22                            BLIJDE INKOMSTSTRAAT     0.000000  0.000000   
23                  BLOKKEN-KRUISHOFSTR. (WILR.PL)     0.000000  0.000000   
24                                      BOEKENBERG     0.000000  0.000000   
25                                   BOEKENBERGLEI     0.000000  0.000000   
26                                  BOEKENBERGPARK     0.000000  0.000000   
27                               BOELAERPARK-NOORD     0.000000  0.000000   
28                                 BONDGENOTENLAAN     0.000000  0.000000   
29                                         BOOLEEG     0.000000  0.000000   
30                    BOOMSE STWG-BEERSCHOT (KIEL)     0.000000  0.000000   
31                       BORGERHOUT - GEMEENTEHUIS     0.000000  0.000000   
32                            BOTERLAAR - SILSBURG     0.000000  0.000000   
33                                    BOTERLAARHOF     0.000000  0.000000   
34                                        BOVEN-LO     0.000000  0.000000   
35                               BRABANCONNESTRAAT     0.000000  0.000000   
36                                            BREM     0.000000  0.000000   
37                                     BRUINE VELD     0.000000  0.000000   
38                                           BRUUL     0.000000  0.000000   
39                  C. TEICHMANN PLAATS (ZUIDWIJK)     0.000000  0.000000   
40                                 CAMPUS HEVERLEE     0.000000  0.000000   
41                             CENTRALE GEVANGENIS     0.000000  0.000000   
42                           CENTRALE WERKPLAATSEN     0.000000  0.000000   
43                  CHARLES DE COSTERLAAN(L.OEVER)     0.000000  0.000000   
44                         CHARLOTTALEI (OOSTWIJK)     0.000000  0.000000   
45                                         COLLEGE     0.000000  0.000000   
46                                        CONFORTA     0.000000  0.000000   
47                                        CRUYSLEI     0.000000  0.000000   
48          DAGERAADPLAATS - OOSTSTATIE (OOSTWIJK)     0.000000  0.000000   
49                         DAM (DAM - SCHIJNPOORT)     0.000000  0.000000   
50                   DAM- LOBROEKDOK (SCHIJNPOORT)     0.000000  0.000000   
51                  DAMBRUGGESTRAA

Let's explore the top 5 venues per neighborhood

In [94]:
num_top_venues = 5

for hood in city_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = city_grouped[city_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----'T EILANDJE----
                      venue  freq
0               Coffee Shop  0.16
1              Cocktail Bar  0.11
2  Mediterranean Restaurant  0.05
3               Supermarket  0.05
4                    Bistro  0.05


----'T FORT----
                   venue  freq
0                  Trail  0.33
1                   Park  0.33
2           Cocktail Bar  0.33
3        Paintball Field  0.00
4  Outdoors & Recreation  0.00


----'T LAAR----
                venue  freq
0             Dog Run   0.4
1  Athletics & Sports   0.2
2                 Bar   0.2
3              Bakery   0.2
4         Zoo Exhibit   0.0


----'T MESTPUTTEKE----
              venue  freq
0  Doner Restaurant   0.1
1              Pool   0.1
2  Greek Restaurant   0.1
3              Café   0.1
4    Ice Cream Shop   0.1


----ALBERTPARK (OOSTWIJK)----
          venue  freq
0          Park  0.29
1   Coffee Shop  0.14
2  Tram Station  0.14
3       Dog Run  0.14
4           Gym  0.14


----AN-HAVEN/VORMINGSSTATION----
      

In [95]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [96]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = city_grouped['Neighborhood']

for ind in np.arange(city_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(city_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0            'T EILANDJE           Coffee Shop          Cocktail Bar   
1                'T FORT                 Trail                  Park   
2                'T LAAR               Dog Run                   Bar   
3         'T MESTPUTTEKE                  Pool      Greek Restaurant   
4  ALBERTPARK (OOSTWIJK)                  Park                   Gym   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Event Space                  Café        Sandwich Place   
1          Cocktail Bar                   Zoo           Film Studio   
2                Bakery    Athletics & Sports           Event Space   
3        Ice Cream Shop   Sporting Goods Shop                  Café   
4           Supermarket          Tram Station           Coffee Shop   

      6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Mediterranean Restaurant             Laser Tag                Bistro   
1               Event Space               Factory    Falafel Restaurant   
2        Falafel Restaurant                  Farm        Farmers Market   
3               Pizza Place      Doner Restaurant                Bakery   
4                   Dog Run                   Zoo        Farmers Market   

  9th Most Common Venue 10th Most Common Venue  
0            Restaurant              Nightclub  
1                  Farm         Farmers Market  
2  Fast Food Restaurant            Film Studio  
3         Garden Center             Restaurant  
4           Event Space                Factory

In [97]:
city_grouped.head()

Neighborhood  Zoo Exhibit  ATM  Adult Boutique  \
0            'T EILANDJE          0.0  0.0             0.0   
1                'T FORT          0.0  0.0             0.0   
2                'T LAAR          0.0  0.0             0.0   
3         'T MESTPUTTEKE          0.0  0.0             0.0   
4  ALBERTPARK (OOSTWIJK)          0.0  0.0             0.0   

   African Restaurant  American Restaurant  Aquarium  Argentinian Restaurant  \
0                 0.0                  0.0       0.0                     0.0   
1                 0.0                  0.0       0.0                     0.0   
2                 0.0                  0.0       0.0                     0.0   
3                 0.0                  0.0       0.0                     0.0   
4                 0.0                  0.0       0.0                     0.0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0          0.0         0.0                  0.0                   0.0   
1          0.0         0.0                  0.0                   0.0   
2          0.0         0.0                  0.0                   0.0   
3          0.0         0.0                  0.0                   0.0   
4          0.0         0.0                  0.0                   0.0   

   Asian Restaurant  Athletics & Sports  Auto Garage  BBQ Joint  Bagel Shop  \
0               0.0                 0.0          0.0        0.0         0.0   
1               0.0                 0.0          0.0        0.0         0.0   
2               0.0                 0.2          0.0        0.0         0.0   
3               0.0                 0.0          0.0        0.0         0.0   
4               0.0                 0.0          0.0        0.0         0.0   

   Bakery  Bar  Baseball Field  Basketball Court  Bath House  Beach  \
0     0.0  0.0             0.0               0.0         0.0    0.0   
1     0.0  0.0             0.0               0.0         0.0    0.0   
2     0.2  0.2             0.0               0.0         0.0    0.0   
3     0.1  0.0             0.0               0.0         0.0    0.0   
4     0.0  0.0             0.0               0.0         0.0    0.0   

   Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0        0.0              0.0       0.0          0.0         0.0   
1        0.0              0.0       0.0          0.0         0.0   
2        0.0              0.0       0.0          0.0         0.0   
3        0.0              0.0       0.0          0.0         0.0   
4        0.0              0.0       0.0          0.0         0.0   

   Belgian Restaurant  Bike Rental / Bike Share  Bike Shop  Bike Trail  \
0                 0.0                       0.0        0.0         0.0   
1                 0.0                       0.0        0.0         0.0   
2                 0.0                       0.0        0.0         0.0   
3                 0.0                       0.0        0.0         0.0   
4                 0.0                       0.0        0.0         0.0   

     Bistro  Board Shop  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0  0.052632         0.0            0.0        0.0               0.0       0.0   
1  0.000000         0.0            0.0        0.0               0.0       0.0   
2  0.000000         0.0            0.0        0.0               0.0       0.0   
3  0.000000         0.0            0.0        0.0               0.0       0.0   
4  0.000000         0.0            0.0        0.0               0.0       0.0   

   Bowling Alley  Bowling Green  Brasserie  Brazilian Restaurant  \
0            0.0            0.0        0.0                   0.0   
1            0.0            0.0        0.0                   0.0   
2            0.0            0.0        0.0                   0.0   
3            0.0            0.0        0.0                   0.0   
4            0.0            0.0        0.0                   0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  B

Finally, the clustering. After a bit of trial and error, we set the cluster to 8. It's a bit high due to some neighborhoods being not residential in nature, at all, such as the harbour or parks. Otherwise all residential neighborhoods would be clustered together and there would not be much interest for us in this exercise

In [98]:
# set number of clusters
kclusters = 8

city_grouped_clustering = city_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(city_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[:]

array([4, 3, 4, 4, 3, 4, 7, 4, 4, 4, 4, 4, 4, 4, 7, 0, 6, 4, 4, 4, 4, 4,
       4, 4, 3, 4, 3, 7, 4, 4, 4, 4, 7, 4, 0, 4, 3, 4, 4, 4, 4, 4, 4, 3,
       4, 4, 3, 4, 4, 4, 4, 4, 4, 4, 4, 1, 4, 4, 4, 3, 1, 7, 4, 4, 5, 4,
       4, 4, 0, 4, 4, 7, 2, 4, 4, 4, 7, 4, 4, 4, 4, 4, 4, 3, 4, 4, 4, 2,
       3, 4, 4, 4, 4, 4, 4, 4, 3, 1, 4, 4, 4, 4, 4, 4, 4, 4, 4, 1, 7, 4,
       4, 4, 4, 7, 1, 3, 7, 3, 4, 0, 4, 4, 7, 4, 4, 4, 4, 4, 4, 3, 4, 4,
       4, 0, 4, 4, 4, 4, 4, 4, 4, 4, 6, 4, 3, 4, 4, 4, 4, 4, 4, 1, 4, 4,
       0, 4, 4, 4, 1, 5, 4, 4, 4, 4, 4, 4, 4, 4, 4, 0, 2, 2, 4, 4, 4, 4,
       4, 5, 4, 2, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 1, 4, 4, 4, 4, 2, 1, 1,
       4, 4, 4, 4, 3, 4, 4, 4, 4, 5, 1, 4, 4, 4, 4, 4, 3, 4, 1, 4, 4, 4,
       4, 7, 0, 1, 4, 4, 7, 4, 4, 4, 4, 7, 4, 4, 3, 4, 7, 4, 3, 7, 4, 4,
       1, 4, 4, 2, 4, 0, 4, 4, 4, 4, 0, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
       4, 4, 4, 4, 7, 4, 0, 4, 7, 4, 4, 4, 1, 4, 4, 4, 4, 4, 4, 4, 4, 3,
       4, 4, 7, 4, 4, 4, 4, 5, 4, 4, 4, 4, 4, 4, 3,

In [102]:
# to be used if we rerun the below
neighborhoods_venues_sorted.drop(columns=['Cluster Labels'], inplace=True)

In [103]:
# add clustering labels --> Manually change Cluster Labels name to make it work each iteration
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

city_merged = Cities

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
city_merged = city_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Name')

city_merged.head() # check the last columns!

Code1                                          Name   Code2  \
0  1100212MQ                                      STABROEK  110021   
1  11002A00-  ANTWERPEN KERN - OUDE STAD (SPAANSE WALLEN )  11002A   
2  11002A01-                      KLAPDORP - BROUWERSVLIET  11002A   
3  11002A02-                  GROENPLAATS (SPAANSE WALLEN)  11002A   
4  11002A03-                   HOOGSTRAAT (SPAANSE WALLEN)  11002A   

                                 Name2 Municipality    Area_ha  Peri_m  \
0          WIJZIGING VAN GEMEENTEGRENS    Antwerpen  81.007781  5228.0   
1  1-2-3-4 ADMINISTR. WIJK OF DISTRICT    Antwerpen  22.257464  2208.0   
2  1-2-3-4 ADMINISTR. WIJK OF DISTRICT    Antwerpen  13.816001  1753.0   
3  1-2-3-4 ADMINISTR. WIJK OF DISTRICT    Antwerpen  10.901108  1343.0   
4  1-2-3-4 ADMINISTR. WIJK OF DISTRICT    Antwerpen   9.244515  1212.0   

   Density  Population       Lon        Lat                  Geometry  \
0        0           0  4.341878  51.329844  POINT (4.34188 51.32984)   
1      125        2788  4.400889  51.222503  POINT (4.40089 51.22250)   
2      115        1595  4.403601  51.225234  POINT (4.40360 51.22523)   
3       49         537  4.402588  51.219115  POINT (4.40259 51.21911)   
4      114        1053  4.398159  51.219379  POINT (4.39816 51.21938)   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             4.0                  Port       Harbor / Marina   
1             4.0    Belgian Restaurant                 Plaza   
2             4.0           Coffee Shop               Gay Bar   
3             4.0           Coffee Shop          Cocktail Bar   
4             4.0          Cocktail Bar                   Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Fast Food Restaurant  Ethiopian Restaurant           Event Space   
1           Coffee Shop            Restaurant    Italian Restaurant   
2                   Bar             Nightclub           Snack Place   
3             Bookstore             Juice Bar                   Bar   
4           Coffee Shop                Bistro              Beer Bar   

  6th Most Common Venue 7th Most Common Venue    8th Most Common Venue  \
0               Factory    Falafel Restaurant                     Farm   
1       Harbor / Marina                Church     Ethiopian Restaurant   
2      Greek Restaurant                  Café  Health & Beauty Service   
3                Church        Clothing Store             Burger Joint   
4              Wine Bar                 Hotel       Falafel Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0        Farmers Market            Film Studio  
1                  Café      Fish & Chips Shop  
2      Asian Restaurant    Empanada Restaurant  
3              Beer Bar          Deli / Bodega  
4        Ice Cream Shop      French Restaurant

In [104]:
city_merged_nonan = city_merged.dropna(subset=['Cluster Labels'])

### Results

In the next three maps, we can see each city separately

In [108]:
address = 'Antwerpen, Belgium'

geolocator = Nominatim(user_agent="ca_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city_merged_nonan['Lat'], city_merged_nonan['Lon'], city_merged_nonan['Name'], city_merged_nonan['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [113]:
address = 'Leuven, Belgium'

geolocator = Nominatim(user_agent="ca_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city_merged_nonan['Lat'], city_merged_nonan['Lon'], city_merged_nonan['Name'], city_merged_nonan['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

The geograpical coordinate of Antwerpen, Belgium are 51.2211097, 4.3997081.
The geograpical coordinate of Leuven, Belgium are 50.879202, 4.7011675.


In [ ]:
address = 'Genk, Belgium'

geolocator = Nominatim(user_agent="ca_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of {} are {}, {}.'.format(address, latitude, longitude))

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city_merged_nonan['Lat'], city_merged_nonan['Lon'], city_merged_nonan['Name'], city_merged_nonan['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

For future reference only, below the code for checking individually the results for each cluster

In [214]:
city_merged_nonan.loc[city_merged_nonan['Cluster Labels'] == 3, city_merged_nonan.columns[[1] + list(range(5, city_merged_nonan.shape[1]))]]

Name     Area_ha  Peri_m  Density  Population       Lon  \
147  EK-EKERSE PUTTEN  219.689868  9105.0        0           0  4.399198   

           Lat                  Geometry  Cluster Labels  \
147  51.282581  POINT (4.39920 51.28258)             3.0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
147                  Park           Zoo Exhibit   Egyptian Restaurant   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
147   Empanada Restaurant    English Restaurant           Escape Room   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
147  Ethiopian Restaurant           Event Space               Exhibit   

    10th Most Common Venue  
147                Factory

### Discussion

There is a clear clustering of more central locations in each of the three cities, versus clusters outside the city center. Perhaps the clustering is not clear enough. This could be solved by grouping further the venues categories, for instance, all restaurants together, all cultural venues together, all sport venues together... That could bring a better view on the different neighborhoods and potentially needing less clusters.
ADD ON THE DIFFERENCE BETWEEN CITIES

### Conclusion
where you conclude the report.